$$V(x,y)=-V_0\left(\cos^2(kx)+\cos^2(ky)\right)-\frac{V_1}{4}\left(\cos(2kx)-\cos(2ky)\right)^2$$

$$V_n=-V_0\begin{pmatrix}0&0&0&0&0\\0&0&\frac14&0&0\\0&\frac14&1&\frac14&0\\0&0&\frac14&0&0\\0&0&0&0&0\end{pmatrix}-\frac{V_1}{4}\begin{pmatrix}0&0&\frac14&0&0\\0&-\frac12&0&-\frac12&0\\\frac14&0&1&0&\frac14\\0&-\frac12&0&-\frac12&0\\0&0&\frac14&0&0\end{pmatrix}$$

In [1]:
import numpy as np
import tensorflow as tf

import plotly.graph_objects as go

In [2]:
num_quasimomenta = 99

max_momentum_site = 5
num_momentum_sites = (2*max_momentum_site + 1) ** 2

In [3]:
quasimomentum = np.mgrid[0:2:num_quasimomenta*1j,
                         0:2:num_quasimomenta*1j].reshape(2,-1).T

momentum_site = np.mgrid[-max_momentum_site:max_momentum_site+1:1,
                         -max_momentum_site:max_momentum_site+1:1].reshape(2,-1).T

momentum = 2*momentum_site + quasimomentum[:, np.newaxis]
kinetic = np.linalg.norm(momentum, axis=-1)**2

momentum_site_change = momentum_site[:, np.newaxis] - momentum_site
max_momentum_site_change = 2 * max_momentum_site

In [4]:
def render_momentum_site_potential(depths):
    return (-(depths[0]/4) * np.pad(
        np.array([[0, 1, 0],
                  [1, 4, 1],
                  [0, 1, 0]]), 1)
            -(depths[1]/16) *
        np.array([[ 0,  0, +1,  0,  0],
                  [ 0, -2,  0, -2,  0],
                  [+1,  0, +4,  0, +1],
                  [ 0, -2,  0, -2,  0],
                  [ 0,  0, +1,  0,  0]]))

In [5]:
def spatial_from_momentum_site_potential(momentum_site_potential, num_points=100):
    spatial_potential = tf.math.real(tf.signal.rfft2d(tf.signal.ifftshift(tf.pad(momentum_site_potential, tf.constant(np.full((2, 2), num_points))))))
    return tf.concat([spatial_potential, tf.reverse(spatial_potential, [-1])], -1)

def tile_spatial_potential(spatial_potential, periods=1):
    return tf.tile(spatial_potential, np.full((2,), periods))

In [7]:
momentum_site_potential = render_momentum_site_potential(np.array([1, 1.07]) * 34.5)
spatial_potential = spatial_from_momentum_site_potential(momentum_site_potential)

figure = go.Figure(data=[go.Surface(z=tile_spatial_potential(spatial_potential, 2))])
figure.update_layout(autosize=False, width=750, height=750)
figure.show()

In [8]:
def compute_dispersion(momentum_site_potential):
    max_potential_momentum_site = (momentum_site_potential.shape[0] - 1) // 2

    potential = np.pad(momentum_site_potential, max_momentum_site_change - max_potential_momentum_site)[
        momentum_site_change[:, :, 0] + max_momentum_site_change,
        momentum_site_change[:, :, 1] + max_momentum_site_change,
    ]

    energy = tf.linalg.diag(kinetic) + potential[np.newaxis, ...]

    dispersion = tf.reshape(tf.linalg.eigvalsh(energy), (num_quasimomenta, num_quasimomenta, num_momentum_sites))

    return dispersion

In [16]:
depths = np.array([1, 1.15]) * 40

momentum_site_potential = render_momentum_site_potential(depths)

dispersion = compute_dispersion(momentum_site_potential)

figure = go.Figure(data=[go.Surface(z=dispersion[:, :, band], showscale=False, name=fr"${band}$") for band in range(0, 3)])
figure.update_layout(autosize=False, width=750, height=750, 
    # title=fr"$\text{{Dispersion }}E(k)\text{{ @ }}V_0/E_R={depth:.1f}$",
    # xaxis=dict(title=r"$\text{Quasimomentum }k_x/k_L$"),
    # yaxis=dict(title=r"$\text{Quasimomentum }k_y/k_L$"),
    # zaxis=dict(title=r"$\text{Energy }E/E_R$")
)
figure.show()